# Arctop's data scientist exercise

### By Koren Gast 

In [2]:
import pandas as pd
from utils import butter_bandpass_filter, determine_window_size, build_features_by_window
from models.logisticModel import LogisticModel
from models.randomForest import RandomForest
from models.adaBoost import AdaBoost
from models.neuralNetwork import MLP
from models.lstm import LSTM_model
import numpy as np
from scipy.fftpack import fft
from scipy.signal import butter, sosfilt, argrelextrema

%matplotlib inline

In [3]:
CHANNELS = ['EEG1', 'EEG2', 'EEG3', 'EEG4', 'EEG5']

In [4]:
raw_data = pd.read_csv('data.txt',
                       names=CHANNELS + ['Y'],
                       delimiter=r"\s+")
# raw_data = pd.read_csv('data_example.txt',
#                            names=CHANNELS + ['Y'],
#                            delimiter=r"\s+")


Split the datat to train, validation and test:

In [5]:
s = raw_data.shape[0]
raw_train_data = raw_data.iloc[:int(s/2)]
raw_val_data = raw_data.iloc[int(s/2):int(3*s/4)].reset_index(drop=True)
raw_test_data = raw_data.iloc[int(3*s/4):].reset_index(drop=True)


In [6]:
print('Train:')
print(raw_train_data.describe())
print('Validation:')
print(raw_val_data.describe())
print('Test:')
print(raw_test_data.describe())

Train:
                EEG1           EEG2           EEG3           EEG4  \
count  127224.000000  127224.000000  127224.000000  127224.000000   
mean       -0.638391      -0.774241      -0.431818      -0.725321   
std         9.101242       7.901728       8.654187       8.180087   
min       -45.416530     -43.226526     -49.510866     -54.202203   
25%        -6.310509      -5.708042      -5.897423      -5.780383   
50%        -0.889678      -0.819691      -0.690493      -0.811558   
75%         4.972801       4.226785       4.749305       4.382157   
max        41.120556      33.138238      35.069590      31.006209   

                EEG5              Y  
count  127224.000000  127224.000000  
mean       -0.256168       0.244875  
std         8.202641       0.586250  
min       -50.777321       0.000000  
25%        -5.464141       0.000000  
50%        -0.581529       0.000000  
75%         4.596721       0.000000  
max        35.997237       2.000000  
Validation:
               EE

               EEG1          EEG2          EEG3          EEG4          EEG5  \
count  63612.000000  63612.000000  63612.000000  63612.000000  63612.000000   
mean      -0.349835     -0.575538     -0.125934     -0.470783     -0.047828   
std        8.964942      8.126312      8.538127      8.091119      8.282847   
min      -32.801828    -27.827510    -28.727365    -33.106541    -34.345633   
25%       -5.970452     -5.619549     -5.522578     -5.538989     -5.399444   
50%       -0.404125     -0.580503     -0.343707     -0.499711     -0.350293   
75%        5.249513      4.493760      4.990296      4.623543      4.955208   
max       37.046769     33.146789     34.307284     31.215793     31.527478   

                  Y  
count  63612.000000  
mean       0.262529  
std        0.610594  
min        0.000000  
25%        0.000000  
50%        0.000000  
75%        0.000000  
max        2.000000  


## Denoise
From quick research I founded several interferences might noisying the data such as: eye blinks, eyes movments, alpha waves, motor activities and more. There are several techniques to deal with those interfernences. In the scope of this project I'll only use band-pass filter.

According to
**Ramoser, H., Muller-Gerking, J., & Pfurtscheller, G. (2000). Optimal spatial filtering of single trial EEG during imagined hand movement. IEEE transactions on rehabilitation engineering, 8(4), 441-446.**, the used band should be: 8-30 Hz

According to
**Blankertz, B., Tomioka, R., Lemm, S., Kawanabe, M., & Muller, K. R. (2008). Optimizing spatial filters for robust EEG single-trial analysis. IEEE Signal processing magazine, 25(1), 41-56**, the used band should be: 7-30 Hz

So, for denosing the data I'll use a butterwotrh band pass filter to filter signals below 7 Hz and above 30 Hz:

In [7]:
LOW_CUT = 7
HIGH_CUT = 30
SAMPLING_RATE = 1.0 / 512.0  # Samples spacing


Get the filtered data:

In [9]:
train_data = dict()
val_data = dict()
test_data = dict()
for c in CHANNELS:
    train_data[c] = butter_bandpass_filter(raw_train_data[c], LOW_CUT, HIGH_CUT, 1/SAMPLING_RATE)
    val_data[c] = butter_bandpass_filter(raw_val_data[c], LOW_CUT, HIGH_CUT, 1/SAMPLING_RATE)
    test_data[c] = butter_bandpass_filter(raw_test_data[c], LOW_CUT, HIGH_CUT, 1/SAMPLING_RATE)
train_data = pd.DataFrame(train_data)
val_data = pd.DataFrame(val_data)
test_data = pd.DataFrame(test_data)
train_data['Y'] = raw_train_data['Y']
val_data['Y'] = raw_val_data['Y']
test_data['Y'] = raw_test_data['Y']


## Feature extraction



First, I need to determine the **window size** which I will calculate. To do so, I decided to find the shortest sequnce of the same 'Y' and take 2 less than it.

In [10]:

WINDOW_SIZE = determine_window_size(raw_data)
print('Window size:')
print(WINDOW_SIZE)


Window size:
51


### Features
The features (calculated for each channel) are:

1. min, max, mean and gap - The min, max and mean for each window. The gap is max-min

2. min_diff, max_diff,... - min, nax, mean and gap after calculating diff

3. peaks, ft_peak1, ... , ft_peak_val1, ... - Those features are calculating using fourier transform


In [12]:
features_list = ['min', 'max', 'mean', 'gap',
                 'min_diff', 'max_diff', 'mean_diff', 'gap_diff',
                 '#peaks', 'ft_peak1', 'ft_peak2', 'ft_peak3', 'ft_peak4',
                 'ft_peak_val1', 'ft_peak_val2', 'ft_peak_val3', 'ft_peak_val4']

### The slide of the window (stride) and how to predict?
#### My original idea:
**For the train data:** The window (of a size of 51) is moving one by one on the training data, I'll call it srtide=1. If all 'Y' values are the same in the current window, it calculates the features. (e.g. for a sequance of 53 of signal data rows where Y=2, I will have 3 features rows. One for signal rows 1-51, one for 2-52 and one for 3-53)

**For the validation\test data:** Again I'll use stride=1, however it is cheating to check somthing about the 'Y' so features would be calculate for every window (and not just for windows with the same 'Y'). This way, when I'm preforming a prediction for a features row, it is a prediction for 51 signal rows and because stride=1 it means every signal row is getting 51 predictions. That is why, for evert signal row, I will use the prediction with the highest probability


#### What was implemented (Under utils.build_features_by_window):
Due to limitations of time and hardware, instead of using stride=1, I used stride=window_size.

**Implications on the train data:** I have much less data. For example, if in the signal data there are 53 rows with Y=2 and than 103 rows with Y=0 I will have 1 features row for Y=2 (two signal rows won't be used) and 2 features rows for Y=0 (one signal row won't be used). Total of 3 features rows instead of 105 (53+103-51) features rows in my original, yet expensive, idea.

**Implications on the validation\test data:** T


In [16]:
# train_features = build_features_by_window(train_data, WINDOW_SIZE, features_list, CHANNELS, SAMPLING_RATE)
# train_features.to_csv('train_features.csv')
train_features = pd.read_csv('train_features.csv')

In [17]:
# val_features = build_features_by_window(val_data, WINDOW_SIZE, features_list,
#                                         CHANNELS, SAMPLING_RATE, is_train=False)
# val_features.to_csv('val_features.csv')
val_features = pd.read_csv('val_features.csv')


In [18]:
# test_features = build_features_by_window(test_data, WINDOW_SIZE, features_list,
#                                          CHANNELS, SAMPLING_RATE, is_train=False)
# test_features.to_csv('test_features.csv')
test_features = pd.read_csv('test_features.csv')

In [19]:
X = np.array(train_features.drop('Y', axis=1))
y = np.array(train_features['Y'])
val_X = np.array(val_features.drop('Y', axis=1))
val_y = np.array(val_features['Y'])

In [20]:
log_model = LogisticModel()
log_model.fit(X, y)
log_conf = log_model.evaluate_on_signal(val_X, val_data, WINDOW_SIZE)

C:\Users\koren\PycharmRep\Arctop\models\model.py:30: FutureWarning: set_value is deprecated and will be removed in a future release. Please use .at[] or .iat[] accessors instead
  preds_df.set_value(j, ['Y_preds', 'Y_probs'], [pred, prob])


[[52426    40     0]
 [ 5145   149    52]
 [ 5567    66   167]]


In [29]:
val_data['predictions'] = preds_df['Y_preds']
val_data['acc'] = val_data.apply(lambda row: 1 if row['Y']==row['predictions'] else 0, axis=1)

In [30]:
val1 = val_data[val_data['Y']==1]
val2 = val_data[val_data['Y']==2]

In [32]:
np.mean(val2['acc'])

0.16482758620689655

In [21]:
rf_model = RandomForest(10)
rf_model.fit(X, y)
rf_conf = rf_model.evaluate(val_X, val_y)


[[1022    4    2]
 [  95    9    0]
 [  94    4   17]]


In [16]:
boost_model = AdaBoost(10)
boost_model.fit(X, y)
boost_conf = boost_model.evaluate(val_X, val_y)

[[1015    4    9]
 [ 101    3    0]
 [  89    5   21]]


In [17]:
mlp_model = MLP()
mlp_model.fit(X, y)
mlp_conf = mlp_model.evaluate(val_X, val_y)

[[1021    2    5]
 [  96    5    3]
 [ 102    3   10]]


In [41]:
__author__ = "Koren Gast"
from models.model import GenModel
from keras.layers import Dense, Input, LSTM
from keras.models import Model
from sklearn.preprocessing import MinMaxScaler
from keras.utils import to_categorical

class LSTM_model(GenModel):
    def __init__(self):
        super().__init__()
        self.model = self.build()
        self.model.compile(loss='categorical_crossentropy', optimizer='adam')
        self.scaler = MinMaxScaler(feature_range=(0,1))
        self.name = "LSTM"

    def build(self):
        NUM_CHANNELS = 5
        inputs = Input(shape=(1, NUM_CHANNELS))
        X = LSTM(64)(inputs)
        outputs = Dense(3, activation='softmax')(X)
        model = Model(inputs=inputs, outputs=outputs)
        print(model.summary())
        return model

    def fit(self, X, y, epochs=1, batch_size=15):
        X = self.scaler.fit_transform(X)
        X = X.reshape(X.shape[0], 1, X.shape[1])
        y = to_categorical(y)
        self.model.fit(X, y, epochs=epochs, batch_size=batch_size)

    def predict(self, X):
        X = self.scaler.transform(X)
        X = X.reshape(X.shape[0], 1, X.shape[1])
        raw_preds = self.model.predict(X)
        preds = np.argmax(raw_preds, axis=1)
        probs = np.max(raw_preds, axis=1)
        return preds, probs


In [44]:
X = np.array(train_data.drop('Y', axis=1))
y = np.array(train_data['Y'])
lstm = LSTM_model()
lstm.fit(X, y, epochs=100, batch_size=50)

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_13 (InputLayer)        (None, 1, 5)              0         
_________________________________________________________________
lstm_12 (LSTM)               (None, 64)                17920     
_________________________________________________________________
dense_10 (Dense)             (None, 3)                 195       
Total params: 18,115
Trainable params: 18,115
Non-trainable params: 0
_________________________________________________________________
None


Epoch 1/100


    50/127224 [..............................] - ETA: 1:40:37 - loss: 1.1050

   650/127224 [..............................] - ETA: 7:52 - loss: 1.0683   

  1200/127224 [..............................] - ETA: 4:20 - loss: 1.0326

...

125350/127224 [============================>.] - ETA: 0s - loss: 0.5090

125900/127224 [============================>.] - ETA: 0s - loss: 0.5089

126450/127224 [============================>.] - ETA: 0s - loss: 0.5089

127000/127224 [============================>.] - ETA: 0s - loss: 0.5088

127224/127224 [==============================] - 13s 99us/step - loss: 0.5089


In [46]:
lstm_conf = lstm.evaluate(X, y)

[[105324     22    824]
 [ 10600     35    319]
 [  8444     14   1642]]


## Future work
1. different windows


## Future work
1. different windows
